### A Tutorial on HVO_Sequence Representation for Drums

Topics covered in this tutorial:
    
    1. Manually Creating HVO_Sequence Scores
    2. Plotting HVO_Sequence Scores
    3. Synthesizing HVO_Sequence Scores
    4. Data Conversions: From/To NoteSequence and From/To Midi Conversion

In [1]:
# The main implementation of HVO_Sequence dtype can be found in hvo_sequence.hvo_seq
from hvo_sequence.hvo_seq import HVO_Sequence

# A number of drum mappings are stored in hvo_sequence.drum_mappings.
from hvo_sequence.drum_mappings import ROLAND_REDUCED_MAPPING

# Numpy will be used in this tutorial as well
import numpy as np

# For displaying plots or playing audio in Jupyter
import IPython


True


------------------------------------------------------------
------------------------------------------------------------
### An Overview of HVO_Sequence Scores

HVO_Sequence score have a numer of essential fields:
    
    1. drum_mapping:     a dictionary of grouped midi notes and corresponding names 
                         {..., "Snare": [38, 37, 40], ...}
                         This dictionary groups a number of pitchs together into a single drum voice
                         If you don't want any grouping, use GM1 Mapping available in hvo_sequence.drum_mappings
    
    2. tempos:           a list of custom Tempo datatype (specified in hvo_sequence.custom_dtypes). 
                         This datatype has two essential fields:
                             I. time_step: The grid index (not actual time in seconds) where tempo is activated
                             II. qpm:  The qpm tempo activated at time step
                         Note. The first Tempo should be activated at time_step=0
          
    3. time_signatures:  a list of custom Time_Signature datatype (specified in hvo_sequence.custom_dtypes). 
                         This datatype has 4 essential fields:
                             I. time_step: The grid index (not actual time in seconds) where tempo is activated
                             II. numerator: Numerator of the time_signature
                             III. denominator: Denominator of the time_signature
                             IV. beat_division_factors: A list of integers specifying the number of subdivisions 
                                 to be used in each beat 
                                 Each factor needs to be either binary (power of 2) or divisible by 3
                             
                         Note. The first Time_Signature must be activated at time_step=0
    4.hvo:               A numpy.ndarray of shape (number of time_steps, 3 * number of grouped drum voices)
                         This is the main score (similar to the specification in Magenta's GrooVAE)
                         (Lets assume 9 drum voice groups as specified in ROLAND_REDUCED_MAPPING)
                         hvo[:,:9] --> binary of 0 or 1 where 1 denotes a drum voice being hit
                         hvo[:,9:18] --> any real value between 0 and 1 where the value denotes the velocity of 
                                         a drum event (1 being loudest)
                         hvo[:,19:26] --> any real value between -0.5 and 0.5 where the value denotes 
                                          the ratio of offset from a given grid line. Ratio calculated based on
                                          distance of the time difference between two given grid lines

------------------------------------------------------------
------------------------------------------------------------
### Example 1. Manually Creating a HVO_Sequence Score

##### step 1. Create an instance of a HVO_Sequence


In [2]:
hvo_seq = HVO_Sequence(drum_mapping=ROLAND_REDUCED_MAPPING)

Right now all fields of hvo_seq are empty except drum_mapping.

To update the fields in hvo_seq, use the builtin parameter setters:

    1. For adding tempos          --> hvo_seq.add_tempo(time_step, qpm)
    2. For adding time_signatures --> hvo_seq.add_time_signature(time_step, numerator, 
                                                   denominator, beat_division_factors)
    3. For inputting score        --> hvo_seq.hvo = a numpy array of (time_steps, 3*n_drum_voices)
    


##### step 2. set tempo and time_signature

Let's start with setting the initial tempo and time_signature. 

    Initial Tempo            --> starts at the very beginning and qpm = 50
    Intitial Time_Signature  --> 4/4 signature at the very beginning, 
                                 each beat divided in 4 subdivisions
                                 (i.e. 16th note resolution grid)
                                            


In [3]:
# Initialize
hvo_seq.add_tempo(0, 50)
hvo_seq.add_time_signature(0, 4, 4, [4]) 

# Lets look into tempos and time_signatures fields
print(hvo_seq.tempos)
print(hvo_seq.time_signatures)


[Tempo = { 
 	 time_step: 0, 
 	 qpm: 50
}]
[Time_Signature = { 
 	 time_step: 0, 
 	 numerator: 4, 
 	 denominator: 4, 
 	 beat_division_factors: [4]
}]


##### step 3. Create a score and add it to the HVO_Sequence instance


In [5]:
hits = np.random.randint(0, 2, (36, 9))
vels = hits * np.random.rand(36, 9)
offs = hits * (np.random.rand(36, 9) - 0.5)

# Add hvo score to hvo_seq instance
hvo_seq.hvo = np.concatenate((hits, vels, offs), axis=1)

# Lets look into a hvo field for the first 4 steps
print("hvo score is: \n", hvo_seq.hvo[:4, :])

hvo score is: 
 [[ 1.          0.          1.          0.          1.          1.
   1.          1.          1.          0.01571898  0.          0.85402534
   0.          0.44952653  0.6293866   0.77397244  0.35394949  0.88977504
   0.08300168 -0.         -0.42205487  0.          0.15691912 -0.35612145
  -0.23236513 -0.37866362 -0.18745127]
 [ 1.          0.          1.          1.          0.          0.
   0.          0.          0.          0.99255981  0.          0.44066373
   0.03974384  0.          0.          0.          0.          0.
  -0.3794685  -0.          0.20066926 -0.09521069  0.         -0.
   0.         -0.          0.        ]
 [ 0.          0.          0.          0.          1.          0.
   1.          1.          1.          0.          0.          0.
   0.          0.24298316  0.          0.47146551  0.89210042  0.23496209
  -0.         -0.          0.          0.         -0.15686    -0.
  -0.22251575  0.04068554 -0.11521564]
 [ 0.          1.          0.      

In [7]:
# Let's look into a give time step of the score
# Note that first 9 values (hits) are 0 or 1
# Next 9 values (velocities) are real values between 0 to 1
# And, last 9 (offsets/utimings) are real values between -0.5, +0.5
hvo_seq.hvo[8]     # or use hvo_seq.hvo[8, :]


array([ 0.        ,  0.        ,  1.        ,  1.        ,  1.        ,
        0.        ,  1.        ,  0.        ,  0.        ,  0.        ,
        0.        ,  0.769489  ,  0.96455187,  0.82389297,  0.        ,
        0.45189117,  0.        ,  0.        ,  0.        ,  0.        ,
        0.31370444, -0.09495697, -0.32476093,  0.        , -0.44369798,
       -0.        ,  0.        ])

##### step 4. Before we starting using this score, let's check and see if there are any fields missing 




In [8]:
ready_to_use = all([hvo_seq.is_hvo_score_available(print_missing=True),
                    hvo_seq.is_drum_mapping_available(print_missing=True),
                    hvo_seq.is_time_signatures_available(print_missing=True),
                    hvo_seq.is_tempos_available(print_missing=True),
                   ])

print("Are the necessary fields specified: {}".format(ready_to_use))
print("HVO_Sequence instance is ready to use" if ready_to_use else "There are essential fields missing from the score")

Are the necessary fields specified: True
HVO_Sequence instance is ready to use


Now, that all necessary fields are available, we can plot/export/synthesize the score

##### Plotting
You can plot the scores as piano rolls using an internal implementation based on Bokeh plots

In [10]:
#reset_output()
figure = hvo_seq.to_html_plot(filename="test/misc/test1.html", 
                              show_figure=True,
                              show_tempo=True, tempo_font_size="8pt",
                              show_time_signature=True, time_signature_font_size="8pt",
                              minor_grid_color = "black", minor_line_width=0.1,
                              major_grid_color = "blue", major_line_width=0.5,
                              downbeat_color = "red", downbeat_line_width=2,
                              width=800, height=400)



##### Export to Note_Sequence and MIDI

You can save/convert the scores to midi file or pretty_midi or note_sequence

In [11]:
ns = hvo_seq.to_note_sequence()
print(ns)

time_signatures {
  numerator: 4
  denominator: 4
}
tempos {
  qpm: 50.0
}
notes {
  pitch: 36
  velocity: 1
  start_time: 0.02490050392084241
  end_time: 0.17490050392084233
  instrument: 9
  is_drum: true
}
notes {
  pitch: 42
  velocity: 108
  end_time: 0.1499999999999999
  instrument: 9
  is_drum: true
}
notes {
  pitch: 43
  velocity: 57
  start_time: 0.047075735140721504
  end_time: 0.1970757351407214
  instrument: 9
  is_drum: true
}
notes {
  pitch: 47
  velocity: 79
  end_time: 0.1499999999999999
  instrument: 9
  is_drum: true
}
notes {
  pitch: 50
  velocity: 98
  end_time: 0.1499999999999999
  instrument: 9
  is_drum: true
}
notes {
  pitch: 49
  velocity: 44
  end_time: 0.1499999999999999
  instrument: 9
  is_drum: true
}
notes {
  pitch: 51
  velocity: 113
  end_time: 0.1499999999999999
  instrument: 9
  is_drum: true
}
notes {
  pitch: 36
  velocity: 126
  start_time: 0.18615944942665366
  end_time: 0.33615944942665354
  instrument: 9
  is_drum: true
}
notes {
  pitch: 4

In [12]:
pm = hvo_seq.save_hvo_to_midi(filename="test/misc/test1.mid", midi_track_n=9)
print(pm)

##### Synthesize to audio

You can synthesize the score using an internal synthesizer built using fluidSynth

In [13]:
audio = hvo_seq.save_audio(filename="test/misc/test1.wav", sr=44100,
                           sf_path="hvo_sequence/soundfonts/Standard_Drum_Kit.sf2")
print(audio)
IPython.display.Audio("test/misc/test1.wav")


[ 0.          0.         -0.00022227 ...  0.00066681  0.
  0.        ]


------------------------------------------------------------
------------------------------------------------------------
### Example 2. Multiple Tempos and Time_Signatures HVO_Sequence Score

The HVO_Sequence implementation supports multiple tempos and time_signatures as well as mixed beat division factors


In [14]:
# Tempo Change middle of first measure
hvo_seq.add_tempo(8, 20)  

# Time signature change at the beginning of second measure
# Also, the grid resolution is mix of triplet and binary after this point
hvo_seq.add_time_signature(12, 6, 8, [3,2]) 

print(hvo_seq.tempos)
print(hvo_seq.time_signatures)

[Tempo = { 
 	 time_step: 0, 
 	 qpm: 50
}, Tempo = { 
 	 time_step: 8, 
 	 qpm: 20
}]
[Time_Signature = { 
 	 time_step: 0, 
 	 numerator: 4, 
 	 denominator: 4, 
 	 beat_division_factors: [4]
}, Time_Signature = { 
 	 time_step: 12, 
 	 numerator: 6, 
 	 denominator: 8, 
 	 beat_division_factors: [3, 2]
}]


In [15]:
figure = hvo_seq.to_html_plot(filename="test/misc/test2.html", 
                              show_figure=True,
                              show_tempo=True, tempo_font_size="8pt",
                              show_time_signature=True, time_signature_font_size="8pt",
                              minor_grid_color = "black", minor_line_width=0.1,
                              major_grid_color = "blue", major_line_width=0.5,
                              downbeat_color = "blue", downbeat_line_width=2,
                              width=800, height=400)

In [16]:
pm = hvo_seq.save_hvo_to_midi(filename="test/misc/test1.mid", midi_track_n=9)
print(pm)

audio = hvo_seq.save_audio(filename="test/misc/test1.wav", sr=44100,
                           sf_path="hvo_sequence/soundfonts/Standard_Drum_Kit.sf2")
print(audio)
IPython.display.Audio("test/misc/test1.wav")

[ 0.          0.         -0.00022401 ... -0.00044803 -0.00134409
  0.        ]
